In [1]:
# download data
!cd ./data
!wget http://csr.bu.edu/ftp/visda17/clf/train.tar
!tar xvf train.tar

/bin/bash: line 0: cd: ./data: No such file or directory
--2021-12-22 17:14:36--  http://csr.bu.edu/ftp/visda17/clf/train.tar
Resolving csr.bu.edu (csr.bu.edu)... 128.197.11.70
Connecting to csr.bu.edu (csr.bu.edu)|128.197.11.70|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 7698031104 (7.2G) [application/x-tar]
Saving to: ‘train.tar’

train.tar           100%[===================>]   7.17G  37.2MB/s    in 3m 45s  

2021-12-22 17:18:24 (32.7 MB/s) - ‘train.tar’ saved [7698031104/7698031104]

train/plant/src_5_24-3-1__282_236_150.png
train/train/src_3_2836__248_236_150.png
train/bus/src_2_02924116_6f2436c52c0a78947d2d874548544c4e__180_236_150.png
train/bus/src_2_02924116_2f9c60f6eb0a4ac1b4b1329ea0ab3ba4__112_123_150.png
train/horse/src_5_9-2-1__231_236_165.png
train/knife/src_3_1758__112_123_150.png
train/horse/src_3_1552__265_236_165.png
train/train/src_1_04468005_4f0ee7b0644ef0ad930027595c4fa0af__214_236_150.png
train/bicycle/src_3_103__27_10_165.png
train/aer

Create overall split by angle (mappings/all), each file is named cyaw{x}.txt, it contains a list of img file names that correspond to images with camera yaw angle x

In [11]:
# there are 20 camera yaw values for each category, from 10, 27, ... to 333
# rotation around vertical axis
# about 7600 samples per cyaw, total ~150000 samples
# each image is 216*384, 3 rgb channels

# create mapping files, write to txt
import numpy as np
files = {}
i = 0
cyaw_vals = np.arange(10,350,17)
for cyaw in cyaw_vals:
    curf = open(f"mappings/all/cyaw{cyaw}.txt", "a")
    files[str(cyaw)] = curf

for root, directories, filenames in os.walk('train/'):
    for filename in filenames: 
        fullname = os.path.join(root, filename)
        try:
            curcyaw = filename.split("__")[1].split("_")[0]
            # write to the corresponding mapping file
            files[curcyaw].write(fullname)
            files[curcyaw].write("\n")
            i += 1
        except:
            pass

for f in files:
    files[f].close()
print(i)

152397


split into train and test sets - for each camera yaw angle, random 80-20 split, put into mappings/train and mappings/test folders. Within train/ or test/, each file is cyaw{x}.txt, contains a list of image paths that correspond to the train/test images for camera yaw angle x

In [ ]:
# mappings/test and mappings/train are 20-80 random split of each rotation (camera yaw) angle
# split mappings for each shift to train and val

import os
import random

mlist = os.listdir("mappings/all")

for f in mlist[2:]:
    print(f)
    fstream = open("mappings/all/"+f,"r")
    imglist = fstream.read().splitlines()
    # shuffle
    random.shuffle(imglist)
    test_size = int(0.2*len(imglist))
    testf = open("mappings/test/"+f,"a")
    for ele in imglist[:test_size]:
        testf.write(ele+"\n")
    testf.close()
    trainf = open("mappings/train/"+f,"a")
    for ele in imglist[test_size:]:
        trainf.write(ele+"\n")
    trainf.close()


Below is for inspecting data

In [133]:
# for inspection

def parser(name): # returns [cate_id, obj_id, camera_yaw, light_yaw, camera_pitch]
    try:
        angles = name.split("__")[1][:-4] # strip .png at the end
    except:
        return []
    elements_list = angles.split("_")
    return [int(elements_list[0]), int(elements_list[1]), int(elements_list[2])]

def add_or_create(dict, ele):
    if ele in dict:
        dict[ele] = dict[ele]+1
    else:
        dict[ele] = 1

cyaws={}
lyaws={}
cpitches={}
for n in os.listdir("train/aeroplane"):
    try:
        cyaw, lyaw, cpitch = parser(n)
        add_or_create(cyaws,cyaw)
        add_or_create(lyaws,lyaw)
        add_or_create(cpitches, cpitch)
    except:
        pass

In [134]:
cyaws

{10: 716,
 112: 716,
 129: 716,
 146: 716,
 163: 716,
 180: 716,
 197: 716,
 214: 716,
 231: 716,
 248: 716,
 265: 713,
 27: 716,
 282: 716,
 299: 712,
 316: 716,
 333: 712,
 44: 716,
 61: 716,
 78: 716,
 95: 716}